## Import libraries

In [30]:
import pandas as pd
import numpy as np
import datetime
from datetime import timedelta

import plotly.graph_objects as go


## Data location

In [32]:
data_loc = "S://Docs//Personal//MAEVE//Data//"

## Pull data

In [33]:
path = data_loc + "BTC_price_1h.csv"
df = pd.read_csv(path)

print(f"Data shape: {df.shape}")

print(f"Date range: {df.Datetime.min()} - {df.Datetime.max()}")

Data shape: (17017, 7)
Date range: 2021-02-01 00:00:00+00:00 - 2023-01-20 13:00:00+00:00


## MAEVE class

In [1]:
class MAEVE:
    
    # Data location
    data_loc = "S://Docs//Personal//MAEVE//Data//"
    
    # Initial USD value for backtest
    init_cash = 10000.00
    
    # Collect all backtest results
    backtest_df = pd.DataFrame(columns=['strategy_id','timeframe','MA1','MA2','stoploss','streaklim','cooldown','profit/loss'])
    
    def __init__(self, MA1, MA2, stoploss, streaklim, cooldown):
        
        # Initialize strategy parameters
        self.MA1 = MA1
        self.MA2 = MA2
        self.stoploss = stoploss
        self.streaklim = streaklim
        self.cooldown = cooldown
        
        # Read in data
        self.df = pd.read_csv(data_loc + "BTC_price_1h.csv")
        
        # Initialize the strategy variables
        self.current_position = None  # "buy" or "sell"
        self.cash = init_cash  # Starting cash
        self.sats = 0  # Starting BTC

        # Strategy logging
        self.trades_df = pd.DataFrame()
        self.strat_sats = []
        self.strat_usd = []

        # Position management
        self.stop_price = 0
        self.streak = 0
        self.idle = 0
    
    
    def reinit(self, ):
        pass
    
    
    def calc_MA(self, df, timeperiod):
        df[f'MA{timeperiod}'] = df['Close'].rolling(window=timeperiod).mean()
        return df
    
    
    def log_trade(self, row, pos, cash, sats, init_cash=100):

        df = pd.DataFrame()
        df['Datetime'] = [row['Datetime']]
        df['price'] = [row['Close']]
        df['tradeType'] = [pos]
        df['cash'] = [cash]
        df['sats'] = [sats]
        df['profit/loss'] = np.where(df['sats'] > 0,
                                        (df['sats']*df['price']) - init_cash, df['cash'] - init_cash)
        return df
    
    
    def hodl_dca_perf(self, df, init_cash):
        
        hodl_buy = round(init_cash / df['Close'][0], 8)
        df['hodl_sats'] = hodl_buy
        df['hodl_usd'] = df['hodl'] * df['Close']

        dcaamt = init_cash // 1000
        dcabuy = len(df) // 1000

        df['tmp_rownum'] = list(range(1, len(df)+1))
        df['tmp_dcabuyind'] = np.where(df['tmp_rownum'] % dcabuy == 0, 1, 0)

        df['tmp_dcabuys'] = 0
        df['tmp_dcabuys'] = np.where(df['tmp_dcabuyind'] == 1, round(dcaamt / df['Close'][0], 8),
                                    df['tmp_dcabuys'])

        df['dca_sats'] = df['tmp_dcabuys'].cumsum()
        
        df['tmp_dcanumbuys'] = df['tmp_dcabuyind'].cumsum()
        
        df['dca_usd'] = (df['dca'] * df['Close']) + \
                        (init_cash - (df['tmp_dcanumbuys']*dcaamt))
        
        remCols = [col for col in df.columns if 'tmp' in col]
        df.drop(columns=remCols, inplace=True)
        
        return df


    
    def exec_buy(self, ):
        pass
    
    def exec_sell(self, ):
        pass
    
    def exec_cooldown(self, ):
        pass
    
    def plot_strategy_comparison(self,):
        pass

    def plot_strategy_price_overlay(self,):
        pass

    
    def run_backtest(self):
        
        # Iterate over the rows of the dataframe
        for index, row in self.df.iterrows():
            
            ############
            # Cooldown
            ############
            
            if self.streak >= self.streaklim:
                
                self.idle +=1
                self.strat_sats.append(row_sats)
                self.strat_usd.append(row_usd)
                
                if self.idle >= self.cooldown:
                    self.streak = 0
                    self.idle = 0
                    
                continue
            
            
            #######################
            # Position management
            #######################
            
            # Check stop loss trigger
            if row['Close'] < self.stop_price and self.current_position == "buy":
                
                # Update position
                self.current_position = "sell"
                self.cash = round(self.sats * row['Close'], 2)
                self.sats = 0
                
                # Log trade
                self.trades_df = pd.concat([self.trades_df, self.log_trade(row, self.current_position, self.cash, self.sats)])
                
                # Update streak
                self.streak += 1
                

            ###############
            # BUY signal
            ###############
            
            # Check if the MA1 is higher than the MA2
            if row[self.MA1] > row[self.MA2]:
                # If we're not currently holding any BTC, buy BTC
                if self.current_position != "buy":
                    
                    # Update position
                    self.current_position = "buy"
                    self.sats = round(self.cash / row['Close'], 8)
                    self.cash = 0
                    
                    # Position management
                    self.stop_price = round((1-self.stoploss) * row['Close'], 2)
                    
                    # Log trade
                    self.trades_df = pd.concat([self.trades_df, self.log_trade(row, self.current_position, self.cash, self.sats)])
            
            
            ###############
            # SELL signal  
            ###############
                    
            # Check if the MA1 is lower than the MA2
            elif row[self.MA1] < row[self.MA2]:
                # If we're currently holding BTC, sell
                if self.current_position == "buy":
                    
                    # Update position
                    self.current_position = "sell"
                    self.cash = round(self.sats * row['Close'], 2)
                    self.sats = 0
                    
                    # Log trade
                    self.trades_df = pd.concat([self.trades_df, self.log_trade(row, self.current_position, self.cash, self.sats)])
                    
            
            # Record row
            row_sats = self.sats
            row_usd = self.cash
            self.strat_sats.append(row_sats) 
            row_usd = (row_sats * row['Close']) + (row_usd)
            self.strat_usd.append(row_usd)

        self.df['maeve_sats'] = self.strat_sats
        self.df['maeve_usd'] = self.strat_usd

    



NameError: name 'pd' is not defined

In [ ]:
# Set parameters

MA1 = 'MA12'
MA2 = 'MA24'

stoploss = 0.05
streaklim = 5
cooldown = 24

In [ ]:
# Initialize the strategy variables
current_position = None  # "buy" or "sell"
cash = init_cash  # Starting cash
sats = 0  # Starting BTC

# Strategy logging
trades_df = pd.DataFrame()
strat_sats = []
strat_usd = []

# Position management
stop_price = 0
streak = 0
idle = 0

# Iterate over the rows of the dataframe
for index, row in df.iterrows():
    
    ############
    # Cooldown
    ############
    
    if streak >= streaklim:
        
        idle +=1
        strat_sats.append(row_sats)
        strat_usd.append(row_usd)
        
        if idle >= cooldown:
            streak = 0
            idle = 0
            
        continue
    
    
    #######################
    # Position management
    #######################
    
    # Check stop loss trigger
    if row['Close'] < stop_price and current_position == "buy":
        
        # Update position
        current_position = "sell"
        cash = round(sats * row['Close'], 2)
        sats = 0
        # row_usd = cash

        # Log trade
        trades_df = pd.concat([trades_df, log_trade(row, current_position, cash, sats)])
        
        # Update streak
        streak += 1
        

    ###############
    # BUY signal
    ###############
    
    # Check if the MA1 is higher than the MA2
    if row[MA1] > row[MA2]:
        # If we're not currently holding any BTC, buy BTC
        if current_position != "buy":
            
            # Update position
            current_position = "buy"
            sats = round(cash / row['Close'], 8)
            cash = 0
            # row_sats = sats
            
            # Position management
            stop_price = round((1-stoploss) * row['Close'], 2)
            
            # Log trade
            trades_df = pd.concat([trades_df, log_trade(row, current_position, cash, sats)])
    
    
    ###############
    # SELL signal  
    ###############
              
    # Check if the MA1 is lower than the MA2
    elif row[MA1] < row[MA2]:
        # If we're currently holding BTC, sell
        if current_position == "buy":
            
            # Update position
            current_position = "sell"
            cash = round(sats * row['Close'], 2)
            sats = 0
            # row_usd = cash
            
            # Log trade
            trades_df = pd.concat([trades_df, log_trade(row, current_position, cash, sats)])
            
    
    # Record row
    row_sats = sats
    row_usd = cash
    strat_sats.append(row_sats) 
    row_usd = (row_sats * row['Close']) + (row_usd)
    strat_usd.append(row_usd)

df['maeve_sats'] = strat_sats
df['maeve_usd'] = strat_usd


## Identify test periods

In [36]:
########################
# Bull market
########################
# Feb 01, 2021 - Apr 15, 2021
# Jul 15, 2021 - Nov 15, 2021

########################
# Bear market
########################
# Apr 15, 2021 - Jul 15, 2021
# Nov 15, 2021 - Feb 01, 2022
# Apr 05, 2022 - Jul 01, 2022

########################
# Accumulation/ flat
########################
# Jul 1, 2022 - Nov 1, 2022
# Dec 1, 2022 - Jan 1, 2023 

########################
# Black swan events
########################

# Luna / 3AC / Celcius
# May 1, 2022 - Jul 1, 2022

# FTX
# Nov 1, 2022 - Dec 1, 2022

# Bullish news

# Tesla buy in
# Feb 1, 2021 - Mar 1, 2021

# Futures ETF approval
# Sep 15, 2021 - Nov 1, 2021

# Low volume time periods


In [37]:
df['Datetime'].min()

'2021-02-01 00:00:00+00:00'

In [38]:
df['Datetime'].max()

'2023-01-20 13:00:00+00:00'

## HODL | DCA

In [48]:
df = hodl_dca_perf(df, init_cash=init_cash)
df.shape

(17017, 13)

In [49]:
df.head()

Datetime          Open          High           Low  \
0  2021-02-01 00:00:00+00:00  33114.578125  33114.578125  32384.228516   
1  2021-02-01 01:00:00+00:00  32556.548828  33470.128906  32556.548828   
2  2021-02-01 02:00:00+00:00  33448.257812  33769.785156  33331.187500   
3  2021-02-01 03:00:00+00:00  33654.921875  33712.281250  33531.136719   
4  2021-02-01 04:00:00+00:00  33567.050781  33815.316406  33484.789062   

          Close     Adj Close      Volume      hodl      hodl_usd  dca  \
0  32551.958984  32551.958984           0  0.307201   9999.999886  0.0   
1  33450.535156  33450.535156  1724944384  0.307201  10276.043537  0.0   
2  33655.015625  33655.015625   458350592  0.307201  10338.860176  0.0   
3  33562.886719  33562.886719   782512128  0.307201  10310.558069  0.0   
4  33563.953125  33563.953125  1084145664  0.307201  10310.885670  0.0   

   dca_usd  hodl_sats  dca_sats  
0  10000.0   0.307201       0.0  
1  10000.0   0.307201       0.0  
2  10000.0   0.307201       0.0  
3  10000.0   0.307201       0.0  
4  10000.0   0.307201       0.0

In [50]:
df.tail()

Datetime          Open          High           Low  \
17012  2023-01-20 09:00:00+00:00  20943.105469  20981.156250  20931.226562   
17013  2023-01-20 10:00:00+00:00  20969.929688  20969.929688  20934.496094   
17014  2023-01-20 11:00:00+00:00  20963.314453  20979.398438  20946.828125   
17015  2023-01-20 12:00:00+00:00  20968.013672  21102.187500  20961.205078   
17016  2023-01-20 13:00:00+00:00  21091.349609  21116.476562  21068.138672   

              Close     Adj Close     Volume      hodl     hodl_usd       dca  \
17012  20969.093750  20969.093750          0  0.307201  6441.730134  0.307200   
17013  20961.142578  20961.142578    6860800  0.307201  6439.287525  0.307200   
17014  20968.908203  20968.908203          0  0.307201  6441.673134  0.307200   
17015  21090.339844  21090.339844  195862528  0.307201  6478.977076  0.307200   
17016  21082.660156  21082.660156  129171456  0.307201  6476.617867  0.307507   

           dca_usd  hodl_sats  dca_sats  
17012  6441.705600   0.307201  0.307200  
17013  6439.263000   0.307201  0.307200  
17014  6441.648600   0.307201  0.307200  
17015  6478.952400   0.307201  0.307200  
17016  6473.069793   0.307201  0.307507

## Calculate moving averages

In [52]:
# Calculate MA
MALst = [12, 20, 24, 30, 40, 48, 50, 60, 100, 200]

for MA in MALst:
    df = calc_MA(df, MA)

df.shape


(17017, 23)

## Implement MAEVE strategy

In [ ]:
# Strategy ideas

# Stop losses
# Early exit gains
# Stash profits into usd
# Trailing stop losses
# Lock in profits
# Layer in Support / Resistance 

In [91]:
# Set parameters

MA1 = 'MA12'
MA2 = 'MA24'

stoploss = 0.05
streaklim = 5
cooldown = 24

In [92]:
# Initialize the strategy variables
current_position = None  # "buy" or "sell"
cash = init_cash  # Starting cash
sats = 0  # Starting BTC

# Strategy logging
trades_df = pd.DataFrame()
strat_sats = []
strat_usd = []

# Position management
stop_price = 0
streak = 0
idle = 0

# Iterate over the rows of the dataframe
for index, row in df.iterrows():
    
    ############
    # Cooldown
    ############
    
    if streak >= streaklim:
        
        idle +=1
        strat_sats.append(row_sats)
        strat_usd.append(row_usd)
        
        if idle >= cooldown:
            streak = 0
            idle = 0
            
        continue
    
    
    #######################
    # Position management
    #######################
    
    # Check stop loss trigger
    if row['Close'] < stop_price and current_position == "buy":
        
        # Update position
        current_position = "sell"
        cash = round(sats * row['Close'], 2)
        sats = 0
        # row_usd = cash

        # Log trade
        trades_df = pd.concat([trades_df, log_trade(row, current_position, cash, sats)])
        
        # Update streak
        streak += 1
        

    ###############
    # BUY signal
    ###############
    
    # Check if the MA1 is higher than the MA2
    if row[MA1] > row[MA2]:
        # If we're not currently holding any BTC, buy BTC
        if current_position != "buy":
            
            # Update position
            current_position = "buy"
            sats = round(cash / row['Close'], 8)
            cash = 0
            # row_sats = sats
            
            # Position management
            stop_price = round((1-stoploss) * row['Close'], 2)
            
            # Log trade
            trades_df = pd.concat([trades_df, log_trade(row, current_position, cash, sats)])
    
    
    ###############
    # SELL signal  
    ###############
              
    # Check if the MA1 is lower than the MA2
    elif row[MA1] < row[MA2]:
        # If we're currently holding BTC, sell
        if current_position == "buy":
            
            # Update position
            current_position = "sell"
            cash = round(sats * row['Close'], 2)
            sats = 0
            # row_usd = cash
            
            # Log trade
            trades_df = pd.concat([trades_df, log_trade(row, current_position, cash, sats)])
            
    
    # Record row
    row_sats = sats
    row_usd = cash
    strat_sats.append(row_sats) 
    row_usd = (row_sats * row['Close']) + (row_usd)
    strat_usd.append(row_usd)

df['maeve_sats'] = strat_sats
df['maeve_usd'] = strat_usd


In [93]:
# Create the line plot
fig = go.Figure()
fig.add_trace(go.Scatter(x=df.Datetime, y=df['hodl_usd'], name='HODL'))
fig.add_trace(go.Scatter(x=df.Datetime, y=df['dca_usd'], name='DCA'))
fig.add_trace(go.Scatter(x=df.Datetime, y=df['maeve_usd'], name='MAEVE'))

# Set the title and axis labels
fig.update_layout(title='Strategy returns over time',
                  xaxis_title='Time',
                  yaxis_title='USD')

fig.show()


In [107]:
showCols = ['Datetime', 'Close', 'hodl_usd', 'dca_usd', 'maeve_usd']
results_df = pd.concat([df[showCols].head(1), df[showCols].tail(1)])
results_df.index = ['Start','End']

results_df = pd.concat([results_df, pd.DataFrame({'Datetime': ['',''], 'Close': ['Profit/Loss','%'],
                   'hodl_usd': [results_df['hodl_usd'].End - results_df['hodl_usd'].Start, str(round(((results_df['hodl_usd'].End - results_df['hodl_usd'].Start)*100/init_cash), 2)) + '%'],
                   'dca_usd': [results_df['dca_usd'].End - results_df['dca_usd'].Start, str(round(((results_df['dca_usd'].End - results_df['dca_usd'].Start)/init_cash)*100, 2)) + '%'],
                   'maeve_usd': [results_df['maeve_usd'].End - results_df['maeve_usd'].Start, str(round(((results_df['maeve_usd'].End - results_df['maeve_usd'].Start)*100/init_cash), 2)) + '%']})], ignore_index=True)

results_df.index = ['Start','End','','']
results_df


Datetime         Close     hodl_usd      dca_usd  \
Start  2021-02-01 00:00:00+00:00  32551.958984  9999.999886      10000.0   
End    2023-01-20 13:00:00+00:00  21082.660156  6476.617867  6473.069793   
                                   Profit/Loss -3523.382019 -3526.930207   
                                             %      -35.23%      -35.27%   

          maeve_usd  
Start       10000.0  
End    10752.599416  
         752.599416  
              7.53%

In [108]:
trades_df['profit/loss'].max()


14919.960256984374

In [109]:
trades_df['profit/loss'].min()


7917.52

## Plot price action and strategy

In [39]:
def plot_strategy(df, trades_df):

    # Create a trace for the candle chart
    candle = go.Candlestick(x=df['Datetime'],
                            open=df['Open'],
                            high=df['High'],
                            low=df['Low'],
                            close=df['Close'])

    # Create a trace for the buy points
    buy = go.Scatter(x=trades_df.loc[trades_df.tradeType == "buy"]['Datetime'],
                    y=trades_df.loc[trades_df.tradeType == "buy"]['price'],
                    mode='lines+markers',
                    name='Buy',
                    marker=dict(size=10, color='green'))

    # Create a trace for the sell points
    sell = go.Scatter(x=trades_df.loc[trades_df.tradeType == "sell"]['Datetime'],
                    y=trades_df.loc[trades_df.tradeType == "sell"]['price'],
                    mode='lines+markers',
                    name='Sell',
                    marker=dict(size=10, color='red'))

    # Create the plot
    fig = go.Figure(data=[candle, buy, sell])
    fig.update_layout(yaxis=dict(autorange=True, scaleanchor='y',
                    scaleratio=1, fixedrange=False))
    
    return fig


In [40]:
fig = plot_strategy(df, trades_df)
fig.show()